# Ensemble Methods Using 10 Shot In-Context Learning (ICL) on YTU Cosmos DPO Model

### Import Libraries and Set Paths

In [ ]:
import sys
import os

# Set Constants

# If use Google Colab
use_colab = True
if use_colab:
    from google.colab import drive
    drive.mount('/content/drive')
    ROOT_PATH = "/content/drive/MyDrive/YTUGuz/InContextLearning/"
    os.chdir(ROOT_PATH)
    device = "cuda"
else:
    ROOT_PATH = "G:\Drive'ım\YTUGuz\InContextLearning"
    device = "cpu"

CACHE_PATH = os.path.join(ROOT_PATH, 'cache')
DATA_PATH = os.path.join(ROOT_PATH, 'data')
RAW_DATA_PATH = os.path.join(DATA_PATH, 'raw')
SAMPLE_DATA_PATH = os.path.join(DATA_PATH, 'sample')
OUTPUT_DATA_PATH = os.path.join(DATA_PATH, 'output')

# Create Folders
os.makedirs(CACHE_PATH, exist_ok=True)
os.makedirs(RAW_DATA_PATH, exist_ok=True)
os.makedirs(SAMPLE_DATA_PATH, exist_ok=True)
os.makedirs(OUTPUT_DATA_PATH, exist_ok=True)

for sub_folder in ["arc", "hellaswag", "gsm8k"]:
    os.makedirs(os.path.join(SAMPLE_DATA_PATH, sub_folder), exist_ok=True)
    os.makedirs(os.path.join(OUTPUT_DATA_PATH, sub_folder), exist_ok=True)

Mounted at /content/drive


In [ ]:
import pandas as pd
import numpy as np
import json
from src.utils import missing_values

import torch
from transformers import pipeline

### Read Data

#### GSM8K Turkish Dataset

In [ ]:
df_gsm_10_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "gsm8k", "gsm_10_sample.csv"))
df_gsm_10_sample = df_gsm_10_sample[['question', 'answer', 'short_answer']]
df_gsm_10_sample

question  \
0  Jennie annesinin ofisinde yardım ediyor. Damga...   
1  Ronnie'ye 5 dolar verilirken Rissa'ya üç katı ...   
2  Craig ve kardeşi bildikleri en uzun harfli kel...   
3  Tom'un restoranı her gece 6 rezervasyon alıyor...   
4  Anthony'nin 50 kalemi vardı. Kalemlerinin yarı...   
5  Carver yeni 45 yaşına girdi, bu da onun yaşını...   
6  Elvis'in aylık birikim hedefi 1125 dolar. Nisa...   
7  Theo'nun yaklaşan Güney Afrika iş gezisi için ...   
8  Matteo saatte 55 mil hızla 4 saat seyahat etti...   
9  Dr. Wertz'in okulunda kız öğrencilerin sayısın...   

                                              answer  short_answer  
0  Jennie 60 mektubun üçte birine, yani 60/3=20 m...            10  
1  Rissa'ya 5 doların 3 katı kadar, yani $5 x 3 =...             2  
2  On tur sonunda, Craig bildiği en uzun harfli k...           650  
3  Her masa için yemeklerin maliyeti 2*5=10 dolar...           180  
4  Anthony başlangıçta 50 kaleme sahipti. Kalemle...            10  
5  Carver'ın yaşı 45 olduğuna göre ve bu da onun ...            25  
6  Elvis, Nisan ayında aylık birikim hedefine ula...            50  
7  Theo 6 iş takımı için 6 takım * 100 dolar/takı...          2050  
8  Matteo saatte 55 mil hızla 4 saat boyunca seya...           230  
9  Dr. Wertz'in okulunda kız öğrencilerin sayısı ...            36

In [ ]:
df_gsm_400_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "gsm8k", "gsm_400_sample.csv"))
df_gsm_400_sample = df_gsm_400_sample[['question', 'answer', 'short_answer']]
df_gsm_400_sample.head()

question  \
0  Amca Ben'in dört atı var. Her at öğün başına b...   
1  Bir yerel kasaba genişliyor ve önümüzdeki üç y...   
2  Amber, Micah ve Ahito toplamda 52 mil koştu. A...   
3  İki araba bir otobanda seyahat ediyor. İlk ara...   
4  Hızlı ve Öfkeli serisinden 9 film var, Deepa h...   

                                              answer short_answer  
0  Amca Ben'in dört atı var ve her bir at öğün ba...            4  
1  İlk yıl, kasaba 12 ev inşa edecek. İkinci yıl,...          144  
2  Amber 8 mil koştu.\nMicah, Amber'ın koştuğunun...           16  
3  İki saat sonra, ilk araba 60*2 = <<60*2=120>>1...           20  
4  Deepa, Hızlı ve Öfkeli serisinden olan 9 filmi...            8

#### Arc Turkish Dataset

In [ ]:
df_arc_10_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "arc", "arc_10_sample.csv"))
df_arc_10_sample = df_arc_10_sample[['question', 'answer', 'answerKey']]
df_arc_10_sample

question  \
0  Bilimsel bir araştırmayla hangi soru büyük ola...   
1  Bir gölün yüzeyindeki büyük alg çoğalmaları ha...   
2  Yeni bir organizma keşfedilirse, onu uygun kra...   
3  Neden orman ağaçlarının yapraklarının çoğu ağa...   
4  Bunlardan hangisi yırtıcı hayvanlara karşı sav...   
5  Bir bölgede çok fazla balık avlanması ekosiste...   
6  Hangi su kütlesinde en az bitki ve hayvan yaşı...   
7  Doğrudan güneş ışığına maruz bırakıldığında ha...   
8  Hangi gerçek neden Dünya'da hayat olduğunu ama...   
9  Bilim insanları bir enfeksiyonun nedenini beli...   

                                              answer answerKey  
0  Domates yetiştirmek için gereken ışık miktarı ...         C  
1                                               ışık         C  
2                   organizmanın anatomisinin yapısı         C  
3                       güneş ışığını yakalamak için         B  
4                               yavru geyik lekeleri         B  
5  Balıkları yiyen organizmalar açlık nedeniyle t...         B  
6                                              buzul         C  
7                                    siyah bir kazak         4  
8                 Ay'da çok az su ve oksijen vardır.         C  
9  Bilimsel sonuçlar farklı şekillerde yorumlanab...         B

In [ ]:
df_arc_400_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "arc", "arc_400_sample.csv"))
df_arc_400_sample = df_arc_400_sample[['question', 'answer', 'answerKey']]
df_arc_400_sample.head()

question  \
0  Günümüzde pek çok araba, geçmişte üretilenlere...   
1  Hangi diyagram enerjinin basit bir besin zinci...   
2  Suyun sıcaklığı 10° Celsius'tan -10° Celsius'a...   
3  Suyun bir kısmı tüketime yöneliktir. Su, kayna...   
4  Aşağıdakilerden hangisi insanın kazanılmış bir...   

                                           answer answerKey  
0                                 kaynakları koru         4  
1                      Yapraklar -> Tırtıl -> Kuş         A  
2               Su sıvı halden katı hale dönüşür.         C  
3  Suyu su döngüsünde farklı aşamalara kaydırarak         C  
4                                     Sözlü vurgu         D

#### Hellaswag Turkish Dataset

In [ ]:
df_hellaswag_10_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "hellaswag", "hellaswag_10_sample.csv"))
df_hellaswag_10_sample = df_hellaswag_10_sample[['question', 'answer', 'answerKey']]
df_hellaswag_10_sample

question  \
0  Bir adam oturmuş sigara içiyor. Beyaz bir gita...   
1  [header] Bir ilişkideki duygusal dağınıklığı n...   
2  Spor salonunun zemininde bir cop döndürücü dur...   
3  Suda kask takan, elinde kürek tutan ve kanoda ...   
4  Yaprakları tırmıklayan kişinin etrafında zıpla...   
5  [header] Bir erkeği 10 gün içinde kaybetmekten...   
6  Köpekler sadece frizbiyi yakalamakla kalmıyor,...   
7  Bir adam iki çubuğun üzerinde kendini kaldırıy...   
8  [header] Zorunlu bir dilekçe nasıl sunulur [ti...   
9  [header] Dudaklarınızı nasıl büzersiniz [title...   

                                              answer answerKey  
0                  mikrofona şarkı söylemeye başlar.         D  
1  [alt adımlar] Olumsuz duygularınızı bastırmakt...         C  
2                            sopayı havaya fırlatır.         A  
3  kanonun nasıl kullanılacağı hakkında kameraya ...         A  
4  Yaprakları tırmıklayan, tırmığı ısırmaya çalış...         C  
5  Kız arkadaşları olmasına izin veriliyor, eski ...         A  
6  Köpekler havuza atlarken gösterilirken tarlada...         C  
7                       arkasında oturup izliyorlar.         D  
8  Bu nedenle önergenizi vermeden önce iletişime ...         B  
9  Öpüşmeden hemen önce dudaklarınıza dikkat edin...         C

In [ ]:
df_hellaswag_400_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "hellaswag", "hellaswag_400_sample.csv"))
df_hellaswag_400_sample = df_hellaswag_400_sample[['question', 'answer', 'answerKey']]
df_hellaswag_400_sample.head()

question  \
0  [başlık] Bir moda tasarımı portföyü nasıl hazı...   
1  [header] Okulda nasıl favori öğretmen olunur? ...   
2  [header] Alışveriş merkezinde bir çocuk nasıl ...   
3  Balıkçılık yemleriyle ilgili bir video için ek...   
4  Birçok insan sahilde. Bir adam suya taklalar a...   

                                              answer answerKey  
0  Genel olarak yaratıcı araştırmayı, 3 boyutluyu...         B  
1  Boyunca saygılı bir tavır sergileyin; karşılığ...         B  
2  O, köşede ellerine geçen her şeyle oynuyor ola...         A  
3  Buzda balık tutmak için kullandıkları farklı y...         B  
4                    bunu birçok farklı kez yapıyor.         C

### Generate Prompt with Few Shot

#### Custom Prompt for GSM8K Dataset

In [ ]:
def generate_prompt_gsm(context_examples, eval_question):

    # prompt = "Sen bir Yapay Zeka Asistanısın."
    # prompt += "Aşağıda birkaç örnek soru ve cevap verilmiştir. Lütfen her soruya verilen cevaplara benzer şekilde cevap verin.\n\n"
    prompt = (
        "Sen bir Yapay Zeka Asistanısın.\n"
        "Aşağıda birkaç örnek soru ve bunlara verilen kısa, net cevaplar verilmiştir.\n"
        "Yeni bir soru sorulacaktır ve cevabınız sadece bir sayı olmalıdır.\n"
        "Lütfen açıklama yapmayın, sadece doğru sayıyı döndürün.\n\n"
    # prompt += "Cevap sadece sayıyı içermeli, hiçbir başka şey eklememelidir. Örneğin: 16"

    )
    for i, row in enumerate(context_examples.itertuples(), 1):
        prompt += f"Soru {i}: {row.question.strip()}\nCevap {i}: {row.short_answer}\n\n"

    # prompt += "Aşağıdaki soruya yukarıdaki gibi cevap verin:\n"
    prompt += "\nŞimdi aşağıdaki soruya yanıt ver:\n"
    prompt += f"Soru: {eval_question}\n"
    prompt += "Lütfen açıklama yapma, cevabınız sadece sayı içersin.\n"
    prompt += "Cevap: "
    return prompt

In [ ]:
prompt = generate_prompt_gsm(context_examples=df_gsm_10_sample, eval_question=df_gsm_400_sample.loc[0, 'question'])
print(prompt)

Sen bir Yapay Zeka Asistanısın.
Aşağıda birkaç örnek soru ve bunlara verilen kısa, net cevaplar verilmiştir.
Yeni bir soru sorulacaktır ve cevabınız sadece bir sayı olmalıdır.
Lütfen açıklama yapmayın, sadece doğru sayıyı döndürün.

Soru 1: Jennie annesinin ofisinde yardım ediyor. Damgalanması gereken 60 mektupluk bir yığını ve zaten damgalanmış mektupların bir yığını var. Damgalanması gereken mektupların üçte birine pul yapıştırıyor. Şimdi damgalanmış mektup yığınında 30 mektup varsa, Jennie başladığında bu yığında kaç mektup vardı?
Cevap 1: 10

Soru 2: Ronnie'ye 5 dolar verilirken Rissa'ya üç katı kadar verildi. Her biri küçük kız kardeşlerine eşit miktarda para verdikten sonra, Rissa'nın parasının 4/5'i kalmıştır. Ronnie'nin parasında ne kadar kalmıştır?
Cevap 2: 2

Soru 3: Craig ve kardeşi bildikleri en uzun harfli kelimeleri sırayla heceliyor ve bu kelimelerdeki harf sayısını sayıyorlar. On tur sonunda, Craig her biri 15 harfli 20 kelime heceler. Eğer Craig'in kardeşi, Craig'den t

#### Custom Prompt for Arc & Hellaswag Dataset

In [ ]:
def generate_prompt_short(context_examples, eval_question):

    prompt = (
        "Sen bir Yapay Zeka Asistanısın.\n"
        "Aşağıda birkaç örnek soru ve bu sorulara verilen kısa, net ve doğru cevaplar bulunmaktadır.\n"
        "Her soruya yalnızca bir şık harfiyle yanıt verilecektir (örneğin: A, B, C, D).\n"
        "Cevap verirken açıklama yapmayınız, sadece doğru şık harfini yazınız.\n\n"
        )

    for i, row in enumerate(context_examples.itertuples(), 1):
        prompt += f"Soru {i}: {row.question}\nCevap {i}: {row.answerKey}\n\n"

    # Değerlendirme sorusunu ve talimatları ekle
    prompt += "\nŞimdi aşağıdaki soruya yanıt ver:\n"
    prompt += f"Soru: {eval_question}\n"
    prompt += "Lütfen sadece doğru şık harfini belirtin (örneğin: A, B, C, D).\n"
    prompt += "Cevap:"
    return prompt

In [ ]:
prompt = generate_prompt_short(context_examples=df_arc_10_sample, eval_question=df_arc_400_sample.loc[0, 'question'])
print(prompt)

Sen bir Yapay Zeka Asistanısın.
Aşağıda birkaç örnek soru ve bu sorulara verilen kısa, net ve doğru cevaplar bulunmaktadır.
Her soruya yalnızca bir şık harfiyle yanıt verilecektir (örneğin: A, B, C, D).
Cevap verirken açıklama yapmayınız, sadece doğru şık harfini yazınız.

Soru 1: Bilimsel bir araştırmayla hangi soru büyük olasılıkla belirlenebilir?
Şıklar:
A. Bir sonraki lotoyu kim kazanacak?
B. Bir sonraki maçı hangi futbol takımı kazanacak?
C. Domates yetiştirmek için gereken ışık miktarı nedir?
D. Hangi dört kuş tüyü türü en güzel renklere sahiptir?
Cevap 1: C

Soru 2: Bir gölün yüzeyindeki büyük alg çoğalmaları hangi abiyotik faktörün dibe ulaşmasını engeller?
Şıklar:
A. su
B. tuz
C. ışık
D. oksijen
Cevap 2: C

Soru 3: Yeni bir organizma keşfedilirse, onu uygun krallığa sınıflandırmak için aşağıdakilerden hangisi büyük olasılıkla kullanılır?
Şıklar:
A. organizmanın rengi
B. organizmanın doğal yaşam alanı
C. organizmanın anatomisinin yapısı
D. organizmanın bulunduğu yer
Cevap 3: C


### Evaluate Model

In [ ]:
def evaluate_model(context_data, eval_data, qa_pipeline, max_new_tokens=256, is_numeric=True):
    terminators = [
        qa_pipeline.tokenizer.eos_token_id,
        qa_pipeline.tokenizer.convert_tokens_to_ids("<|eot_id|>"),
        # qa_pipeline.tokenizer.convert_tokens_to_ids("\n")
    ]

    results = []
    for i, eval_example in enumerate(eval_data.itertuples(), 1):

        # Bağlam ve soruyu birleştir
        if is_numeric:
            prompt = generate_prompt_gsm(context_data, eval_example.question)
        else:
            # prompt = generate_prompt(context_data, eval_example.question)
            prompt = generate_prompt_short(context_data, eval_example.question)

        # Tahmin yap
        output = qa_pipeline(
            prompt,
            max_new_tokens=max_new_tokens,
            eos_token_id=terminators,
            do_sample=True,
            temperature=0.6,
            top_p=0.9,
            # stop_token=["\n"]
        )

        # predicted_answer = output[0]["generated_text"].split("Cevap: ")[-1].strip()
        generated_text = output[0]["generated_text"]
        predicted_answer = generated_text.split("Cevap: ")[-1].strip()
        stop_token = "\n"
        if stop_token in predicted_answer:
            predicted_answer = predicted_answer.split(stop_token)[0].strip()

        # Sonuçları kaydet
        results.append({
            "question": eval_example.question,
            # "true_short_answer": eval_example.short_answer,
            "true_short_answer": eval_example.short_answer if is_numeric else eval_example.answerKey,
            "predicted_short_answer": predicted_answer,
            # "is_correct": predicted_answer == eval_example.answer
        })
        # Her adımda tahmin sonuçlarını yazdır
        print(f"----------  Question {i} ----------")
        print(f"Question\t\t: {eval_example.question}")
        # print(f"True Short Answer\t: {eval_example.short_answer}")
        print(f"True Short Answer\t: {eval_example.short_answer if is_numeric else eval_example.answerKey}")
        print(f"Predicted Short Answer\t: {predicted_answer}")
        print("- - - - - - - - - - - - - - - - - -\n")

    return pd.DataFrame(results)

In [ ]:
print(qa_pipeline.tokenizer.eos_token_id, "<-->", qa_pipeline.tokenizer.convert_tokens_to_ids("<|eot_id|>"))

128009 <--> 128009


### Load Model: YTU CE Cosmos DPO: ytu-ce-cosmos/Turkish-Llama-8b-DPO-v0.1

In [ ]:
model_path = os.path.join(CACHE_PATH, "ytu-ce-cosmos--Turkish-Llama-8b-DPO-v0.1/snapshots/4b04f16749996857d4f81ba0f001552b8e3c0753")
model_id = "ytu-ce-cosmos/Turkish-Llama-8b-DPO-v0.1"

# Cache'de varsa kullan, yoksa indir
if not os.path.exists(model_path):
    print(f"Model Cache'de bulunamadı: {model_path}")
    print(f"Model HuggingFace'ten indiriliyor: {model_id}")
else:
    print(f"Model Cache'den yükleniyor: {model_path}")

# Modeli Yükle
qa_pipeline = pipeline(
    "text-generation",
    model = model_path if os.path.exists(model_path) else model_id,
    # model = model_id,
    model_kwargs = {"torch_dtype": torch.bfloat16},
    device_map = "auto"
)

Model Cache'den yükleniyor: /content/drive/MyDrive/YTUGuz/InContextLearning/cache/ytu-ce-cosmos--Turkish-Llama-8b-DPO-v0.1/snapshots/4b04f16749996857d4f81ba0f001552b8e3c0753


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Device set to use cuda:0


In [ ]:
from transformers import logging

# Show Only Error Messages
logging.set_verbosity_error()

## GSM Prediction

### Using 10 Shot

In [ ]:
gsm_results = evaluate_model(df_gsm_10_sample, df_gsm_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=True)
gsm_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "gsm8k", "gsm_10shot_results.csv"), index=False, encoding='utf-8')

----------  Question 1 ----------
Question		: Amca Ben'in dört atı var. Her at öğün başına beş pound yulaf tüketebilir. Atlarını günde iki kez besler. Bir çuvalda 50 pound yulaf varsa, atlarını beş gün boyunca beslemek için kaç çuval yulafa ihtiyacı vardır?
True Short Answer	: 4
Predicted Short Answer	: 40
- - - - - - - - - - - - - - - - - -

----------  Question 2 ----------
Question		: Bir yerel kasaba genişliyor ve önümüzdeki üç yıl boyunca birkaç yeni ev inşa etmek istiyor. İlk yıl, 12 ev inşa edecekler. Ertesi yıl, bu sayının üç katı kadar ev inşa edecekler. Üçüncü yıl, inşa ettikleri ev sayısını sayacak ve miktarı ikiye katlayacaklar. Kasaba önümüzdeki üç yıl içinde kaç ev inşa etmiş olacak?
True Short Answer	: 144
Predicted Short Answer	: 96
- - - - - - - - - - - - - - - - - -

----------  Question 3 ----------
Question		: Amber, Micah ve Ahito toplamda 52 mil koştu. Amber 8 mil koştu. Micah, Amber'ın koştuğunun 3.5 katı kadar koştu. Ahito kaç mil koştu?
True Short Answer	: 16
P

In [ ]:
gsm_results.head()

question true_short_answer  \
0  Amca Ben'in dört atı var. Her at öğün başına b...                 4   
1  Bir yerel kasaba genişliyor ve önümüzdeki üç y...               144   
2  Amber, Micah ve Ahito toplamda 52 mil koştu. A...                16   
3  İki araba bir otobanda seyahat ediyor. İlk ara...                20   
4  Hızlı ve Öfkeli serisinden 9 film var, Deepa h...                 8   

  predicted_short_answer  
0                     40  
1                     96  
2                   27.5  
3                     40  
4                    8.0

In [ ]:
gsm_results[gsm_results['true_short_answer'] == gsm_results['predicted_short_answer']].shape[0]

29

In [ ]:
gsm_results[gsm_results['true_short_answer'] == gsm_results['predicted_short_answer']].shape[0] / gsm_results.shape[0] * 100

7.249999999999999

In [ ]:
gsm_results['true_short_answer'] = pd.to_numeric(gsm_results['true_short_answer'], errors='coerce')
gsm_results['predicted_short_answer'] = pd.to_numeric(gsm_results['predicted_short_answer'], errors='coerce')
# print(gsm_results.dtypes)

gsm_results[gsm_results['true_short_answer'] == gsm_results['predicted_short_answer']].shape[0] / gsm_results.shape[0] * 100

8.75

### Ensemble

#### Ensemble Method-1: 10 Kere 10 Shot Örnekten Tekrarlı 10’lu Seçimler (Replacement=True)


In [ ]:
for i in range(1, 11):
    print(f"#Ensemble Method-1 Size:10_{i}")
    ens_1_dataset_name = f"gsm_10_sample_ens_1_{i}.csv"
    df_data_ens_1_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "gsm8k", ens_1_dataset_name))
    # print(df_data_ens_1_sample)

    ens_1_result_name = f"gsm_10shot_ens_1_{i}_result.csv"
    gsm_results = evaluate_model(df_data_ens_1_sample, df_gsm_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=True)
    gsm_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "gsm8k", ens_1_result_name), index=False, encoding='utf-8')
    # gsm_results.head()

Streaming output truncated to the last 5000 lines.
----------  Question 368 ----------
Question		: Adrian'ın yaşı Harriet'in yaşının üç katıdır ve Harriet, Zack'in yaşının yarısı kadardır. Harriet şu anda 21 yaşındaysa, üç yıl sonra üçünün ortalama yaşını hesaplayın.
True Short Answer	: 45
Predicted Short Answer	: 27.5
- - - - - - - - - - - - - - - - - -

----------  Question 369 ----------
Question		: Gary haftada iki kez çamaşır yıkar. Her çamaşır yükü için 20 galon su kullanılır ve bir galon suyun maliyeti 0.15 dolardır. Gary yılda çamaşır için suya ne kadar para harcar?
True Short Answer	: 312
Predicted Short Answer	: 312.0
- - - - - - - - - - - - - - - - - -

----------  Question 370 ----------
Question		: Bir sınıfta 40 öğrenci var. Sınıfın yarısı maviyi seviyor. Kalanların dörtte biri yeşili seviyor ve geri kalanlar sarıyı seviyor. Kaç öğrenci sarı rengi seviyor?
True Short Answer	: 15
Predicted Short Answer	: 20
- - - - - - - - - - - - - - - - - -

----------  Question 371 ----

#### Ensemble Method-2: 10 Kere 10 Örnekten 5’li Seçimler (Replacement=False)

In [ ]:
# for i in range(1, 11):
for i in range(5, 11):
    print(f"#Ensemble Method-2 Size:10_{i}")
    ens_2_dataset_name = f"gsm_10_sample_ens_2_{i}.csv"
    df_data_ens_2_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "gsm8k", ens_2_dataset_name))
    # print(df_data_ens_1_sample)

    ens_2_result_name = f"gsm_10shot_ens_2_{i}_result.csv"
    gsm_results = evaluate_model(df_data_ens_2_sample, df_gsm_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=True)
    gsm_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "gsm8k", ens_2_result_name), index=False, encoding='utf-8')
    # gsm_results.head()

Streaming output truncated to the last 5000 lines.
----------  Question 158 ----------
Question		: Carl, Sean'ın dört katı kadar misketi var ve Sean'ın misket sayısı Cal'ınki kadarının yarısı kadar. Eğer Sean'ın 56 misketi varsa, Carl ve Cal'ın toplamda kaç misketi vardır?
True Short Answer	: 336
Predicted Short Answer	: 216
- - - - - - - - - - - - - - - - - -

----------  Question 159 ----------
Question		: Bir ekip 4 boyacı, her gün 3 hafta boyunca günde 3/8 oranında bir malikanede çalıştı. Her bir boyacı kaç saat çalışmış oldu?
True Short Answer	: 189
Predicted Short Answer	: 270.0
- - - - - - - - - - - - - - - - - -

----------  Question 160 ----------
Question		: Helen Almanya'da bir geziye çıktı. 3 gece için bir otel ayırttı ve bu gezi sırasında 7 kez otobüse bindi. Otelde bir gece konaklamanın maliyeti 80 dolar ve her otobüs yolculuğu otelde bir gece konaklamanın fiyatının %10'u kadardı. Helen bu gezi sırasında otel ve otobüs seyahatleri için ne kadar ödedi?
True Short Answer	: 

KeyboardInterrupt: 

#### Ensemble Method-3: 10 Kere 10 Örnekten Tekrarsız 10’lu Seçimler (Replacement=False)

In [ ]:
for i in range(1, 11):
    print(f"#Ensemble Method-3 Size:10_{i}")
    ens_3_dataset_name = f"gsm_10_sample_ens_3_{i}.csv"
    df_data_ens_3_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "gsm8k", ens_3_dataset_name))
    # print(df_data_ens_1_sample)

    ens_3_result_name = f"gsm_10shot_ens_3_{i}_result.csv"
    gsm_results = evaluate_model(df_data_ens_3_sample, df_gsm_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=True)
    gsm_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "gsm8k", ens_3_result_name), index=False, encoding='utf-8')
    # gsm_results.head()

Streaming output truncated to the last 5000 lines.
----------  Question 368 ----------
Question		: Adrian'ın yaşı Harriet'in yaşının üç katıdır ve Harriet, Zack'in yaşının yarısı kadardır. Harriet şu anda 21 yaşındaysa, üç yıl sonra üçünün ortalama yaşını hesaplayın.
True Short Answer	: 45
Predicted Short Answer	: 25.5.
- - - - - - - - - - - - - - - - - -

----------  Question 369 ----------
Question		: Gary haftada iki kez çamaşır yıkar. Her çamaşır yükü için 20 galon su kullanılır ve bir galon suyun maliyeti 0.15 dolardır. Gary yılda çamaşır için suya ne kadar para harcar?
True Short Answer	: 312
Predicted Short Answer	: 312.0
- - - - - - - - - - - - - - - - - -

----------  Question 370 ----------
Question		: Bir sınıfta 40 öğrenci var. Sınıfın yarısı maviyi seviyor. Kalanların dörtte biri yeşili seviyor ve geri kalanlar sarıyı seviyor. Kaç öğrenci sarı rengi seviyor?
True Short Answer	: 15
Predicted Short Answer	: 8
- - - - - - - - - - - - - - - - - -

----------  Question 371 ----

## Hellaswag Prediction

### Using 10 Shot

In [ ]:
hellaswag_results = evaluate_model(df_hellaswag_10_sample, df_hellaswag_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
hellaswag_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "hellaswag", "hellaswag_10shot_results.csv"), index=False, encoding='utf-8')

----------  Question 1 ----------
Question		: [başlık] Bir moda tasarımı portföyü nasıl hazırlanır [başlık] Nelerin dahil edileceğine ilişkin talimatlar veya rehberlik için kontrol edin. [adım] Bir tasarım programına başvuruyorsanız, portföyünüzde ne görmek istediklerine dair iyi bir fikir vermelidirler. Profesyonel bir portföy tasarlıyorsanız açık talimatlarınız olmayabilir.
Şıklar:
A- Ancak, bilgiyi bulmanın ve onu her zamankinden daha iyi derinlemesine açıklamanın gerektiğini unutmayın. Burada size rehberlik etmek için kullanabileceğiniz bazı yararlı rehberlik broşürleri bulunmaktadır.
B- Genel olarak yaratıcı araştırmayı, 3 boyutluyu 2 boyutluya çevirme yeteneğinizi gösteren çizimleri, renk çalışmalarını ve varsa yaptığınız 3 boyutlu çalışmanın fotoğraflarını eklemelisiniz. [alt adımlar] Portföyünüzü, yapmak istediğiniz belirli uygulamaya veya iş türüne göre uyarlayın.
C- Ne ekleyeceğinizden emin değilseniz sorun. Farklı insanlardan öğrenecek deneyiminiz var mı yoksa doğru iş türün

In [ ]:
hellaswag_results.head()

question true_short_answer  \
0  [başlık] Bir moda tasarımı portföyü nasıl hazı...                 B   
1  [header] Okulda nasıl favori öğretmen olunur? ...                 B   
2  [header] Alışveriş merkezinde bir çocuk nasıl ...                 A   
3  Balıkçılık yemleriyle ilgili bir video için ek...                 B   
4  Birçok insan sahilde. Bir adam suya taklalar a...                 C   

  predicted_short_answer  
0                      B  
1                      B  
2                      C  
3                      C  
4                      C

In [ ]:
hellaswag_results[hellaswag_results['true_short_answer'] == hellaswag_results['predicted_short_answer']].shape[0] / hellaswag_results.shape[0] * 100

43.75

### Ensemble

#### Ensemble Method-1: 10 Kere 10 Shot Örnekten Tekrarlı 10’lu Seçimler (Replacement=True)

In [ ]:
for i in range(1, 11):
    print(f"#Ensemble Method-1 Size:10_{i}")
    ens_1_dataset_name = f"hellaswag_10_sample_ens_1_{i}.csv"
    df_data_ens_1_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "hellaswag", ens_1_dataset_name))
    # print(df_data_ens_1_sample)

    ens_1_result_name = f"hellaswag_10shot_ens_1_{i}_results.csv"
    hellaswag_results = evaluate_model(df_data_ens_1_sample, df_hellaswag_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
    hellaswag_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "hellaswag", ens_1_result_name), index=False, encoding='utf-8')
    hellaswag_results.head()

Streaming output truncated to the last 5000 lines.
D- [adım] Ocaktan almadan önce biraz soğumaya bırakın, tereyağı tamamen erimeye başladığında (yaklaşık 5 dakika), ocaktan alın. [başlık] Tereyağını doğru sıcaklığa ısıtın.
True Short Answer	: C
Predicted Short Answer	: B
- - - - - - - - - - - - - - - - - -

----------  Question 347 ----------
Question		: [header] Bir gençlik drama ekibi nasıl kurulur [title] Ne tür bir birlik istediğinizi planlayın. [adım] Komedi mi yapmak istiyorsunuz? Trajediler mi? Modern parçalar mı? Shakespeare? Doğaçlama mı yoksa komedi sporları mı? Altyapı takımınızın hangi yöne gitmesini istediğinizi bildiğinizden emin olun. Bir senaryoya ihtiyacınız varsa birini seçin.
Şıklar:
A- Bir grubunuz olana kadar beklemek ve onların karar vermesini istiyorsanız, en azından aklınızda bir yön bulun. [title] Bu grubun ne kadar süreyle prova yapacağına karar verin.
B- [title] Çok fazla alana ihtiyacınız olacak. [adım] Sıkışık bir odada büyük bir birlik, ortamı biraz gürült

#### Ensemble Method-2: 10 Kere 10 Örnekten 5’li Seçimler (Replacement=False)

In [ ]:
for i in range(1, 11):
    print(f"#Ensemble Method-2 Size:10_{i}")
    ens_2_dataset_name = f"hellaswag_10_sample_ens_2_{i}.csv"
    df_data_ens_2_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "hellaswag", ens_2_dataset_name))
    # print(df_data_ens_1_sample)

    ens_2_result_name = f"hellaswag_10shot_ens_2_{i}_result.csv"
    hellaswag_results = evaluate_model(df_data_ens_2_sample, df_hellaswag_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
    hellaswag_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "hellaswag", ens_2_result_name), index=False, encoding='utf-8')
    # hellaswag_results.head()

Streaming output truncated to the last 5000 lines.
D- [adım] Ocaktan almadan önce biraz soğumaya bırakın, tereyağı tamamen erimeye başladığında (yaklaşık 5 dakika), ocaktan alın. [başlık] Tereyağını doğru sıcaklığa ısıtın.
True Short Answer	: C
Predicted Short Answer	: B
- - - - - - - - - - - - - - - - - -

----------  Question 347 ----------
Question		: [header] Bir gençlik drama ekibi nasıl kurulur [title] Ne tür bir birlik istediğinizi planlayın. [adım] Komedi mi yapmak istiyorsunuz? Trajediler mi? Modern parçalar mı? Shakespeare? Doğaçlama mı yoksa komedi sporları mı? Altyapı takımınızın hangi yöne gitmesini istediğinizi bildiğinizden emin olun. Bir senaryoya ihtiyacınız varsa birini seçin.
Şıklar:
A- Bir grubunuz olana kadar beklemek ve onların karar vermesini istiyorsanız, en azından aklınızda bir yön bulun. [title] Bu grubun ne kadar süreyle prova yapacağına karar verin.
B- [title] Çok fazla alana ihtiyacınız olacak. [adım] Sıkışık bir odada büyük bir birlik, ortamı biraz gürült

#### Ensemble Method-3: 10 Kere 10 Örnekten Tekrarsız 10’lu Seçimler (Replacement=False)

In [80]:
for i in range(1, 11):
    print(f"#Ensemble Method-3 Size:10_{i}")
    ens_3_dataset_name = f"hellaswag_10_sample_ens_3_{i}.csv"
    df_data_ens_3_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "hellaswag", ens_3_dataset_name))
    # print(df_data_ens_1_sample)

    ens_3_result_name = f"hellaswag_10shot_ens_3_{i}_result.csv"
    hellaswag_results = evaluate_model(df_data_ens_3_sample, df_hellaswag_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
    hellaswag_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "hellaswag", ens_3_result_name), index=False, encoding='utf-8')
    # hellaswag_results.head()

Streaming output truncated to the last 5000 lines.
D- [adım] Ocaktan almadan önce biraz soğumaya bırakın, tereyağı tamamen erimeye başladığında (yaklaşık 5 dakika), ocaktan alın. [başlık] Tereyağını doğru sıcaklığa ısıtın.
True Short Answer	: C
Predicted Short Answer	: B
- - - - - - - - - - - - - - - - - -

----------  Question 347 ----------
Question		: [header] Bir gençlik drama ekibi nasıl kurulur [title] Ne tür bir birlik istediğinizi planlayın. [adım] Komedi mi yapmak istiyorsunuz? Trajediler mi? Modern parçalar mı? Shakespeare? Doğaçlama mı yoksa komedi sporları mı? Altyapı takımınızın hangi yöne gitmesini istediğinizi bildiğinizden emin olun. Bir senaryoya ihtiyacınız varsa birini seçin.
Şıklar:
A- Bir grubunuz olana kadar beklemek ve onların karar vermesini istiyorsanız, en azından aklınızda bir yön bulun. [title] Bu grubun ne kadar süreyle prova yapacağına karar verin.
B- [title] Çok fazla alana ihtiyacınız olacak. [adım] Sıkışık bir odada büyük bir birlik, ortamı biraz gürült

## Arc Prediction

### Using 10 Shot

In [ ]:
arc_results = evaluate_model(df_arc_10_sample, df_arc_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
arc_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "arc", "arc_10shot_results.csv"), index=False, encoding='utf-8')

----------  Question 1 ----------
Question		: Günümüzde pek çok araba, geçmişte üretilenlere göre daha iyi yakıt tüketimi sağlayacak şekilde tasarlanmıştır. Bu değişiklik bir ihtiyaçtan kaynaklanmıştır.
Şıklar:
1. geri dönüşüm malzemeleri
2. güvenliği artırmak
3. kimyasallar üretmek
4. kaynakları koru
True Short Answer	: 4
Predicted Short Answer	: D
- - - - - - - - - - - - - - - - - -

----------  Question 2 ----------
Question		: Hangi diyagram enerjinin basit bir besin zincirinde nasıl aktığını en iyi şekilde gösterir?
Şıklar:
A. Yapraklar -> Tırtıl -> Kuş
B. Ağaç -> Kuş -> Tırtıl
C. Yapraklar -> Ağaç -> Tırtıl
D. Tırtıl -> Yapraklar -> Kuş
True Short Answer	: A
Predicted Short Answer	: C
- - - - - - - - - - - - - - - - - -

----------  Question 3 ----------
Question		: Suyun sıcaklığı 10° Celsius'tan -10° Celsius'a değiştiğinde ne olur?
Şıklar:
A. Su katı halden gaz haline dönüşür.
B. Su sıvı halden gaz haline dönüşür.
C. Su sıvı halden katı hale dönüşür.
D. Su katı halden sıvı hale

### Ensemble

#### Ensemble Method-1: 10 Kere 10 Shot Örnekten Tekrarlı 10’lu Seçimler (Replacement=True)

In [82]:
for i in range(1, 11):
    print(f"#Ensemble Method-1 Size:10_{i}")
    ens_1_dataset_name = f"arc_10_sample_ens_1_{i}.csv"
    df_data_ens_1_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "arc", ens_1_dataset_name))
    # print(df_data_ens_1_sample)

    ens_1_result_name = f"arc_10shot_ens_1_{i}_result.csv"
    arc_results = evaluate_model(df_data_ens_1_sample, df_arc_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
    arc_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "arc", ens_1_result_name), index=False, encoding='utf-8')
    # arc_results.head()

Streaming output truncated to the last 5000 lines.
A. Bu bölgenin iklimi ve jeolojisi zamanla değişti.
B. Bu canlılar bir zamanlar soğuk iklimlere daha iyi adapte olmuşlardı.
C. Fosilleşme süreci orijinal materyali büyük ölçüde değiştirdi.
D. Çöpçüler bu canlıların kalıntılarını daha yüksek bölgelere taşıdılar.
True Short Answer	: A
Predicted Short Answer	: A
- - - - - - - - - - - - - - - - - -

----------  Question 347 ----------
Question		: Hangisi kimyasal değişimdir?
Şıklar:
A. Eleman 1 ince bir tabaka halinde dövülmüştür.
B. Element 2 ısıtılır ve sıvıya dönüşür.
C. Element 3 havada durduğunda yeşilimsi bir renk alır.
D. Element 4, ince, kaygan bir toz halinde öğütülür.
True Short Answer	: C
Predicted Short Answer	: B
- - - - - - - - - - - - - - - - - -

----------  Question 348 ----------
Question		: Hayvan diseksiyonu sırasında hangi aparatlara ihtiyaç duyulmaz?
Şıklar:
A. eldivenler
B. gözlük
C. laboratuvar önlüğü
D. güvenlik duşu
True Short Answer	: D
Predicted Short Answer	: A

#### Ensemble Method-2: 10 Kere 10 Örnekten 5’li Seçimler (Replacement=False)

In [83]:
for i in range(1, 11):
    print(f"#Ensemble Method-2 Size:10_{i}")
    ens_2_dataset_name = f"arc_10_sample_ens_2_{i}.csv"
    df_data_ens_2_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "arc", ens_2_dataset_name))
    # print(df_data_ens_1_sample)

    ens_2_result_name = f"arc_10shot_ens_2_{i}_result.csv"
    arc_results = evaluate_model(df_data_ens_2_sample, df_arc_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
    arc_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "arc", ens_2_result_name), index=False, encoding='utf-8')
    # arc_results.head()

Streaming output truncated to the last 5000 lines.
A. Bu bölgenin iklimi ve jeolojisi zamanla değişti.
B. Bu canlılar bir zamanlar soğuk iklimlere daha iyi adapte olmuşlardı.
C. Fosilleşme süreci orijinal materyali büyük ölçüde değiştirdi.
D. Çöpçüler bu canlıların kalıntılarını daha yüksek bölgelere taşıdılar.
True Short Answer	: A
Predicted Short Answer	: A
- - - - - - - - - - - - - - - - - -

----------  Question 347 ----------
Question		: Hangisi kimyasal değişimdir?
Şıklar:
A. Eleman 1 ince bir tabaka halinde dövülmüştür.
B. Element 2 ısıtılır ve sıvıya dönüşür.
C. Element 3 havada durduğunda yeşilimsi bir renk alır.
D. Element 4, ince, kaygan bir toz halinde öğütülür.
True Short Answer	: C
Predicted Short Answer	: B
- - - - - - - - - - - - - - - - - -

----------  Question 348 ----------
Question		: Hayvan diseksiyonu sırasında hangi aparatlara ihtiyaç duyulmaz?
Şıklar:
A. eldivenler
B. gözlük
C. laboratuvar önlüğü
D. güvenlik duşu
True Short Answer	: D
Predicted Short Answer	: B

#### Ensemble Method-3: 10 Kere 10 Örnekten Tekrarsız 10’lu Seçimler (Replacement=False)

In [85]:
for i in range(1, 11):
    print(f"#Ensemble Method-3 Size:10_{i}")
    ens_3_dataset_name = f"arc_10_sample_ens_3_{i}.csv"
    df_data_ens_3_sample = pd.read_csv(os.path.join(SAMPLE_DATA_PATH, "arc", ens_3_dataset_name))
    # print(df_data_ens_1_sample)

    ens_3_result_name = f"arc_10shot_ens_3_{i}_result.csv"
    arc_results = evaluate_model(df_data_ens_3_sample, df_arc_400_sample.head(400), qa_pipeline, max_new_tokens=5, is_numeric=False)
    arc_results.to_csv(os.path.join(OUTPUT_DATA_PATH, "arc", ens_3_result_name), index=False, encoding='utf-8')
    # arc_results.head()

Streaming output truncated to the last 5000 lines.
A. Bu bölgenin iklimi ve jeolojisi zamanla değişti.
B. Bu canlılar bir zamanlar soğuk iklimlere daha iyi adapte olmuşlardı.
C. Fosilleşme süreci orijinal materyali büyük ölçüde değiştirdi.
D. Çöpçüler bu canlıların kalıntılarını daha yüksek bölgelere taşıdılar.
True Short Answer	: A
Predicted Short Answer	: A
- - - - - - - - - - - - - - - - - -

----------  Question 347 ----------
Question		: Hangisi kimyasal değişimdir?
Şıklar:
A. Eleman 1 ince bir tabaka halinde dövülmüştür.
B. Element 2 ısıtılır ve sıvıya dönüşür.
C. Element 3 havada durduğunda yeşilimsi bir renk alır.
D. Element 4, ince, kaygan bir toz halinde öğütülür.
True Short Answer	: C
Predicted Short Answer	: B.
- - - - - - - - - - - - - - - - - -

----------  Question 348 ----------
Question		: Hayvan diseksiyonu sırasında hangi aparatlara ihtiyaç duyulmaz?
Şıklar:
A. eldivenler
B. gözlük
C. laboratuvar önlüğü
D. güvenlik duşu
True Short Answer	: D
Predicted Short Answer	: 